In [1]:
!pip install simpletransformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 250 kB 15.5 MB/s 
     |████████████████████████████████| 9.2 MB 56.6 MB/s 
     |████████████████████████████████| 1.9 MB 45.5 MB/s 
     |████████████████████████████████| 452 kB 57.7 MB/s 
     |████████████████████████████████| 7.6 MB 55.9 MB/s 
     |████████████████████████████████| 5.8 MB 70.6 MB/s 
     |████████████████████████████████| 1.3 MB 52.6 MB/s 
     |████████████████████████████████| 43 kB 2.4 MB/s 
     |████████████████████████████████| 182 kB 60.7 MB/s 
     |████████████████████████████████| 174 kB 68.0 MB/s 
     |████████████████████████████████| 184 kB 64.9 MB/s 
     |████████████████████████████████| 62 kB 1.4 MB/s 
     |████████████████████████████████| 173 kB 67.9 MB/s 
     |████████████████████████████████| 168 kB 63.7 MB/s 
     |████████████████████████████████| 168 kB 65.2 MB/s 
     |█████████████████████████████

# Preprocessing for Course Data

In [2]:
import pandas as pd
data = pd.read_excel('ML_data.xlsx')
data.head()

word    course    sentence      tag
0    master  course 0  Sentence 0        O
1   machine  course 0  Sentence 0  B-skill
2  learning  course 0  Sentence 0  I-skill
3        on  course 0  Sentence 0        O
4    python  course 0  Sentence 0  B-skill

In [3]:
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

In [4]:
data["sentence"] = LabelEncoder().fit_transform(data["sentence"])
data.head()

word    course  sentence      tag
0    master  course 0         0        O
1   machine  course 0         0  B-skill
2  learning  course 0         0  I-skill
3        on  course 0         0        O
4    python  course 0         0  B-skill

In [5]:
data.rename(columns={"sentence":"sentence_id","word":"words","tag":"labels"}, inplace =True)
data["labels"] = data["labels"].str.upper()
data.head()

words    course  sentence_id   labels
0    master  course 0            0        O
1   machine  course 0            0  B-SKILL
2  learning  course 0            0  I-SKILL
3        on  course 0            0        O
4    python  course 0            0  B-SKILL

In [6]:
X = data[["sentence_id","words"]]
Y = data["labels"]

In [7]:
x_train, x_test, y_train, y_test = train_test_split(X,Y, test_size =0.2)

In [8]:
#building up train data and test data
train_data = pd.DataFrame({"sentence_id":x_train["sentence_id"],"words":x_train["words"],"labels":y_train})
test_data = pd.DataFrame({"sentence_id":x_test["sentence_id"],"words":x_test["words"],"labels":y_test})

In [9]:
train_data

sentence_id         words   labels
851           187  transformers        O
371           137          fill        O
668           166    matplotlib  B-SKILL
354           135        models        O
674           167           and        O
...           ...           ...      ...
1614           78    supervised        O
812           182      semantic        O
948            12          what        O
432           141         other        O
902             3            in        O

[1446 rows x 3 columns]

# NER Model Training

In [10]:
from simpletransformers.ner import NERModel,NERArgs

In [11]:
label = data["labels"].unique().tolist()
label

['O', 'B-SKILL', 'I-SKILL']

In [12]:
args = NERArgs()
args.num_train_epochs = 8
args.learning_rate = 1e-4
args.overwrite_output_dir = True
args.train_batch_size = 32
args.eval_batch_size = 32

In [13]:
model = NERModel('bert', 'bert-base-uncased', labels = label, args = args)

Downloading:   0%|          | 0.00/570 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/440M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForTokenClassification: ['cls.predictions.transform.dense.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForTokenClassification were not initialized from the model checkpoint at bert-base-u

Downloading:   0%|          | 0.00/232k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/28.0 [00:00<?, ?B/s]

In [14]:
model.train_model(train_data,eval_data = test_data,acc=accuracy_score)

  0%|          | 0/1 [00:00<?, ?it/s]

Epoch:   0%|          | 0/8 [00:00<?, ?it/s]

Running Epoch 0 of 8:   0%|          | 0/7 [00:00<?, ?it/s]

/usr/local/lib/python3.8/dist-packages/torch/optim/lr_scheduler.py:138: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  warnings.warn("Detected call of `lr_scheduler.step()` before `optimizer.step()`. "


Running Epoch 1 of 8:   0%|          | 0/7 [00:00<?, ?it/s]

...

Running Epoch 4 of 8:   0%|          | 0/7 [00:00<?, ?it/s]

Running Epoch 5 of 8:   0%|          | 0/7 [00:00<?, ?it/s]

Running Epoch 6 of 8:   0%|          | 0/7 [00:00<?, ?it/s]

Running Epoch 7 of 8:   0%|          | 0/7 [00:00<?, ?it/s]

(56, 0.24055398692767735)

In [15]:
result, model_outputs, preds_list = model.eval_model(test_data)
result

  0%|          | 0/1 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/5 [00:00<?, ?it/s]

{'eval_loss': 0.3307304739952087,
 'precision': 0.8775510204081632,
 'recall': 0.7166666666666667,
 'f1_score': 0.7889908256880733}

In [54]:
prediction, model_output = model.predict(["master machine learning on python"])
prediction

  0%|          | 0/1 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

[[{'master': 'O'},
  {'machine': 'B-SKILL'},
  {'learning': 'I-SKILL'},
  {'on': 'O'},
  {'python': 'B-SKILL'}]]

In [58]:
prediction[0][0]

dict

In [31]:
model.save_model('/content/model/NER.exe')

In [89]:
# Most frequent ML skills, was created manually here. Need to find them from the skills file automatically.
ML_skills = ['java', 'python', 'machine', 'learning', 'deep', 'learning', 'data', 'analysis', 'sql', 'data', 'tensorflow']

In [43]:
ML_phrases = pd.read_excel('ML_phrases.xlsx')
ML_phrases

text     course
0                  master machine learning on python r   course 0
1    have a great intuition of many machine learnin...   course 0
2                            make accurate predictions   course 0
3                               make powerful analysis   course 0
4                  make robust machine learning models   course 0
..                                                 ...        ...
189                         multiple linear regression  course 14
190                                logistic regression  course 14
191                                   cluster analysis  course 14
192                                  kmeans clustering  course 14
193                                     decision trees  course 14

[194 rows x 2 columns]

In [60]:
course_dict = {}
for row in ML_phrases.iterrows():
  row = row[1]
  text = row['text']
  words = text.split()
  course = row['course']
  if course not in course_dict:
    course_dict[course] = []
  entities, _ = model.predict([text])
  lst = []
  for i, word in enumerate(words):
    if(entities[0][i][word]!= 'O'):
      lst.append(word)
  course_dict[course].extend(lst)

  0%|          | 0/1 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

In [61]:
course_dict

{'course 0': ['machine',
  'learning',
  'python',
  'machine',
  'learning',
  'machine',
  'learning',
  'machine',
  'learning',
  'reinforcement',
  'learning',
  'nlp',
  'deep',
  'learning',
  'machine',
  'learning',
  'machine',
  'learning'],
 'course 1': ['python',
  'data',
  'science',
  'machine',
  'learning',
  'spark',
  'data',
  'analysis',
  'machine',
  'learning',
  'numpy',
  'pandas',
  'data',
  'analysis',
  'matplotlib',
  'python',
  'seaborn',
  'scikitlearn',
  'machine',
  'learning',
  'natural',
  'language',
  'processing',
  'neural',
  'networks'],
 'course 2': ['data',
  'science',
  'machine',
  'learning',
  'python',
  'data',
  'science',
  'data',
  'data',
  'science',
  'data',
  'science',
  'machine',
  'learning',
  'numpy',
  'processing',
  'python',
  'pandas',
  'data',
  'python',
  'machine',
  'learning',
  'matplotlib',
  'data',
  'python',
  'machine',
  'learning',
  'seaborn',
  'python',
  'data',
  'science',
  'machine',
  '

# Word2Vec Model

In [62]:
import gensim
import pandas as pd
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
nltk.download('punkt')
nltk.download('stopwords')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [63]:
df = pd.read_excel('/content/ML_phrases.xlsx')
df

text     course
0                  master machine learning on python r   course 0
1    have a great intuition of many machine learnin...   course 0
2                            make accurate predictions   course 0
3                               make powerful analysis   course 0
4                  make robust machine learning models   course 0
..                                                 ...        ...
189                         multiple linear regression  course 14
190                                logistic regression  course 14
191                                   cluster analysis  course 14
192                                  kmeans clustering  course 14
193                                     decision trees  course 14

[194 rows x 2 columns]

In [64]:
def tokenize(text):
    tokens = word_tokenize(text)
    return tokens

# Remove stop words
def remove_stop_words(tokens):
    clean_tokens = [token for token in tokens if token.lower() not in stopwords.words('english')]
    return clean_tokens

In [65]:
texts = []

for i in range(len(df)):
  m = tokenize(df.loc[i, 'text'])
  texts.append(remove_stop_words(m))

texts[0:5]

[['master', 'machine', 'learning', 'python', 'r'],
 ['great', 'intuition', 'many', 'machine', 'learning', 'models'],
 ['make', 'accurate', 'predictions'],
 ['make', 'powerful', 'analysis'],
 ['make', 'robust', 'machine', 'learning', 'models']]

In [66]:
model = gensim.models.Word2Vec(texts, window=2, min_count=1, workers=4, batch_words=8)

In [67]:
model.train(texts, total_examples=model.corpus_count, epochs=25)

(25527, 33975)

In [94]:
# Find the most similar courses related to most common ML skills
similarities = {}
for course in course_dict:
  entities = course_dict[course]
  sum = 0
  length = 0
  for word in entities:
    for skill in ML_skills:
      try:
        sum+=model.wv.similarity(w1 = word, w2= skill)
        length+=1
      except:
        print(word, skill)
        continue
  sum/=length #average

  similarities[course] = sum

machine java
machine sql
learning java
learning sql
python java
python sql
machine java
machine sql
learning java
learning sql
machine java
machine sql
learning java
learning sql
machine java
machine sql
learning java
learning sql
reinforcement java
reinforcement sql
learning java
learning sql
nlp java
nlp sql
deep java
deep sql
learning java
learning sql
machine java
machine sql
learning java
learning sql
machine java
machine sql
learning java
learning sql
python java
python sql
data java
data sql
science java
science sql
machine java
machine sql
learning java
learning sql
spark java
spark sql
data java
data sql
analysis java
analysis sql
machine java
machine sql
learning java
learning sql
numpy java
numpy sql
pandas java
pandas sql
data java
data sql
analysis java
analysis sql
matplotlib java
matplotlib sql
python java
python sql
seaborn java
seaborn sql
scikitlearn java
scikitlearn sql
machine java
machine sql
learning java
learning sql
natural java
natural sql
language java
languag

In [95]:
similarities

{'course 0': 0.7889617973547659,
 'course 1': 0.7208280909061432,
 'course 2': 0.7793653588116323,
 'course 3': 0.7217896212026611,
 'course 4': 0.8433338171905942,
 'course 5': 0.6576791703214053,
 'course 6': 0.5235458772392974,
 'course 7': 0.6063363506102267,
 'course 8': 0.7098690269119812,
 'course 9': 0.7794377075301276,
 'course 10': 0.7138900661174162,
 'course 11': 0.6855569467658088,
 'course 12': 0.7099847049900779,
 'course 13': 0.8182447530605175,
 'course 14': 0.6303940061184149}